In [3]:
#  Copyright 2016 The TensorFlow Authors. All Rights Reserved.
#
#  Licensed under the Apache License, Version 2.0 (the "License");
#  you may not use this file except in compliance with the License.
#  You may obtain a copy of the License at
#
#   http://www.apache.org/licenses/LICENSE-2.0
#
#  Unless required by applicable law or agreed to in writing, software
#  distributed under the License is distributed on an "AS IS" BASIS,
#  WITHOUT WARRANTIES OR CONDITIONS OF ANY KIND, either express or implied.
#  See the License for the specific language governing permissions and
#  limitations under the License.
"""Convolutional Neural Network Estimator for MNIST, built with tf.layers."""

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)


def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)


def main(unused_argv):
  # Load training and eval data
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)


if __name__ == "__main__":
    tf.app.run()

E:\Anaconda3\lib\site-packages\h5py\__init__.py:36: FutureWarning: Conversion of the second argument of issubdtype from `float` to `np.floating` is deprecated. In future, it will be treated as `np.float64 == np.dtype(float).type`.
  from ._conv import register_converters as _register_converters


Instructions for updating:
Please use tf.data.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please use alternatives such as official/mnist/dataset.py from tensorflow/models.
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use urllib or similar directly.
Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data\train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data\t10k-labels-idx1-u

INFO:tensorflow:loss = 2.3147473, step = 1
INFO:tensorflow:probabilities = [[0.09826716 0.08736626 0.10300905 0.09989817 0.10387778 0.10431184
  0.11645965 0.09063558 0.09320544 0.10296904]
 [0.09610672 0.1019131  0.10644159 0.09732436 0.08937654 0.10910168
  0.1000024  0.09893586 0.09831636 0.1024814 ]
 [0.09109275 0.09385183 0.09703922 0.10257247 0.10822759 0.10425445
  0.10321511 0.08669978 0.11038258 0.10266427]
 [0.08566827 0.08665294 0.1011618  0.09079713 0.10413378 0.10831208
  0.10692244 0.09504995 0.10384049 0.11746106]
 [0.09870005 0.09047614 0.1061345  0.10952993 0.09228138 0.102354
  0.10919769 0.09365455 0.09498619 0.10268551]
 [0.09146082 0.10411619 0.10842453 0.09053136 0.10248081 0.11014549
  0.10965433 0.09662085 0.09297475 0.09359088]
 [0.10156959 0.08408    0.1070874  0.10317761 0.11397991 0.09552768
  0.1062377  0.08947363 0.09094895 0.1079175 ]
 [0.1012355  0.09756027 0.10704089 0.09426724 0.10020222 0.10296125
  0.10164423 0.0966142  0.09107882 0.10739544]
 [0.093

INFO:tensorflow:global_step/sec: 7.21337
INFO:tensorflow:probabilities = [[0.09312474 0.09879047 0.10256526 0.10110214 0.10358664 0.11569667
  0.09612644 0.08479561 0.10610351 0.09810852]
 [0.08919257 0.10008318 0.11414231 0.09261222 0.09890908 0.09407101
  0.10776877 0.09132671 0.11187646 0.10001773]
 [0.09774284 0.09866604 0.09391903 0.09741355 0.09790998 0.10654696
  0.10780381 0.08518244 0.09962662 0.11518876]
 [0.10129892 0.09510684 0.10969137 0.09121086 0.10803028 0.10459396
  0.09706689 0.09810562 0.09279664 0.10209853]
 [0.08301781 0.10305627 0.10964887 0.10383001 0.09289953 0.09955747
  0.12100551 0.08495122 0.10161147 0.10042179]
 [0.09654235 0.10473162 0.11045264 0.10279614 0.10301618 0.09655431
  0.09581736 0.08800882 0.09554885 0.10653172]
 [0.09630248 0.09419308 0.09965531 0.10008496 0.10117068 0.11488342
  0.09862455 0.0907435  0.09738838 0.10695362]
 [0.09808677 0.07602977 0.09858827 0.10496648 0.12141617 0.10585389
  0.11269085 0.08612874 0.09145255 0.10478641]
 [0.092

INFO:tensorflow:loss = 2.3009048, step = 101 (13.864 sec)
INFO:tensorflow:probabilities = [[0.09342343 0.09799193 0.09951066 0.10689466 0.10012863 0.09515877
  0.11161612 0.08937126 0.09425408 0.1116505 ]
 [0.09379808 0.09886298 0.10875948 0.09226363 0.10562517 0.10162466
  0.10275823 0.09361922 0.09801804 0.10467063]
 [0.08904152 0.10122926 0.1031303  0.0910179  0.10022218 0.11524733
  0.09836022 0.09379134 0.10518607 0.10277383]
 [0.10324397 0.09513052 0.10595761 0.09540626 0.09972702 0.10747636
  0.0993217  0.09605096 0.10165276 0.09603278]
 [0.09358451 0.09915566 0.10553604 0.08275873 0.0793557  0.11139682
  0.13535437 0.08995398 0.10101563 0.10188855]
 [0.10176839 0.08893526 0.1060659  0.09672104 0.1034976  0.09837547
  0.10848173 0.09104803 0.09844545 0.10666107]
 [0.09751295 0.0876893  0.11438344 0.10262392 0.08873899 0.10228049
  0.11241721 0.08545256 0.10407997 0.10482112]
 [0.09320568 0.10442637 0.11200519 0.09551111 0.1008129  0.1051304
  0.09053928 0.10055437 0.0928909  0.1

...

INFO:tensorflow:global_step/sec: 7.40792
INFO:tensorflow:probabilities = [[0.00002782 0.00000004 0.00009854 0.00000024 0.00003099 0.00001156
  0.99982953 0.         0.00000048 0.00000072]
 [0.9987056  0.00000083 0.00046601 0.00008838 0.00000072 0.00017328
  0.00023971 0.0002773  0.00000259 0.00004572]
 [0.00005047 0.00000179 0.00309993 0.00020568 0.00001351 0.05832046
  0.00160127 0.00007582 0.93522686 0.00140422]
 [0.00000016 0.00000054 0.00011695 0.00031855 0.00000007 0.00000008
  0.         0.9986494  0.00000114 0.0009131 ]
 [0.00000162 0.         0.00000174 0.00001126 0.00002463 0.00000947
  0.00000001 0.0019211  0.00003579 0.9979944 ]
 [0.9999943  0.         0.00000308 0.00000002 0.         0.00000093
  0.00000035 0.00000037 0.00000101 0.00000002]
 [0.00108017 0.00045724 0.00161751 0.00068027 0.00019035 0.9609024
  0.03282907 0.00017118 0.00202173 0.00005001]
 [0.0000105  0.00018527 0.05753985 0.9389652  0.00000202 0.00047725
  0.00000117 0.00015842 0.00263223 0.00002823]
 [0.0000

INFO:tensorflow:loss = 0.11773672, step = 19901 (13.494 sec)
INFO:tensorflow:probabilities = [[0.00035727 0.02271143 0.0026951  0.00115385 0.00001907 0.00094253
  0.00000088 0.96334237 0.00296991 0.00580771]
 [0.00022813 0.9841995  0.00276878 0.00069374 0.00140105 0.00025139
  0.00414609 0.00086554 0.00528623 0.00015961]
 [0.00023278 0.00000002 0.00010111 0.00016904 0.00016554 0.00010124
  0.00000106 0.03619048 0.00094627 0.9620924 ]
 [0.00247879 0.00000001 0.00000665 0.00000372 0.0000287  0.0005284
  0.00000019 0.99604994 0.00000081 0.00090279]
 [0.00001057 0.00001744 0.00146905 0.0000613  0.99463177 0.00016483
  0.00238976 0.00054007 0.00014765 0.00056762]
 [0.00067823 0.8542496  0.03542277 0.00058638 0.00005825 0.00004784
  0.00208177 0.00000202 0.10687131 0.00000175]
 [0.00013635 0.00000007 0.00009412 0.00000005 0.00084442 0.00000349
  0.99892044 0.         0.00000045 0.00000062]
 [0.00000889 0.00000006 0.00003915 0.00081072 0.00000014 0.99807006
  0.0009471  0.         0.00012389 

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model\model.ckpt.
INFO:tensorflow:Loss for final step: 0.16965313.
INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2018-06-23-13:55:26
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model\model.ckpt-20000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-06-23-13:55:30
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9693, global_step = 20000, loss = 0.101501815
{'accuracy': 0.9693, 'loss': 0.101501815, 'global_step': 20000}


SystemExit: 

E:\Anaconda3\lib\site-packages\IPython\core\interactiveshell.py:2918: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
